Currents as a function
====================

We want to calculate the currents in sfTrident as a function of the spins and the Lorentz index.
The result would be a class which precomputes the kinematic (spinors etc) and returns a function.

TODO
-------
- implement J1, J2, J3 and test it
- generalize the test (build a function to do the test -> def test(J0func,resJ0fromClass,...))

In [1]:
import sftrident as sf
import sftrident.qft as qft
from sftrident.kinutility import laserPolarisation
import numpy as np
import time
times = {}

The current classes
-----------

In [2]:
class defaultCurrent():
    gammaMu = qft.GammaMatrix()
    
    config = {
        'mass':1.0,
        'a0':1e-4,
        'mode':'bw'
    }
    avialModes = {
        'c': qft.SpinorU,
        'bw': qft.SpinorV
    }
    def __init__(self,q1,q2,k,**kwargs):
        """
        mom ... object of the momenta class
        """
        self.config.update(kwargs)
        self.q1 = q1
        self.q2 = q2
        self.k = k
        self.mode = self.config['mode']
        if not(self.mode in self.avialModes.keys()):
            raise ValueError("There is no build mode called: <%s> !"%(self.mode))
        
        self.mass = self.config['mass']
        self.a0 = self.config['a0']
        self.buildSpinors(self.mode)
        self.polBase =[laserPolarisation(item) for item in [1,2]]
    
    def buildSpinors(self,mode):
        self.sp1 = np.array([qft.SpinorUBar((self.q1,self.mass),s) for s in (1,2)])
        self.sp2 = np.array([self.avialModes[mode]((self.q2,self.mass),s) for s in (1,2)])

class J0(defaultCurrent):
    def __init__(self,q1,q2,k,**kwargs):
        defaultCurrent.__init__(self,q1,q2,k,**kwargs)
    
    def __call__(self,mu,s1,s2):
        return self.sp1[s1]*(self.gammaMu[mu]*self.sp2[s2])

class J1(defaultCurrent):
    def __init__(self,q1,q2,k,**kwargs):
        defaultCurrent.__init__(self,q1,q2,k,**kwargs)
    
    def __call__(self,mu,s1,s2):
        term1 = self.sp1[s1]*(((qft.feyndagg(self.polBase[0])*qft.feyndagg(self.k))*self.gammaMu[mu])*self.sp2[s2])/(self.k*self.q1)
        term2 = self.sp1[s1]*(((self.gammaMu[mu]*qft.feyndagg(self.k))*qft.feyndagg(self.polBase[0]))*self.sp2[s2])/(self.k*self.q2)
        return .5*self.mass*self.a0*(term1 - term2)

class J2(defaultCurrent):
    def __init__(self,q1,q2,k,**kwargs):
        defaultCurrent.__init__(self,q1,q2,k,**kwargs)
    
    def __call__(self,mu,s1,s2):
        term1 = self.sp1[s1]*(((qft.feyndagg(self.polBase[1])*qft.feyndagg(self.k))*self.gammaMu[mu])*self.sp2[s2])/(self.k*self.q1)
        term2 = self.sp1[s1]*(((self.gammaMu[mu]*qft.feyndagg(self.k))*qft.feyndagg(self.polBase[1]))*self.sp2[s2])/(self.k*self.q2)
        return .5*self.mass*self.a0*(term1 - term2)

Test $J_0$
==

In [3]:
def BuildGrid(ss,p1x,p1y,p1m,p2x,p2y,p2m):
    SS, P1x, P1y, P1m, P2x, P2y, P2m = np.meshgrid(ss,p1x,p1y,p1m,p2x,p2y,p2m,indexing='ij')
    return [SS,P1x,P1y,P1m,P2x,P2y,P2m]

ssInit = np.array([3.353])
#p1_x = np.linspace(0.0,3.5,3)
p1_x = np.random.uniform(0.0,3.5,10)
#print "p1_x: %s"%p1_x
#p1_y = np.linspace(0.0,3.5,3)
p1_y = np.random.uniform(0.0,3.5,10)
#print "p1_y: %s"%p1_y
#p1_m = np.linspace(0.0,3.5,20)
p1_m = np.random.uniform(0.0,3.5,20)
#print "p1_m: %s"%p1_m

#p2_x = np.linspace(0.0,3.5,3)
p2_x = np.random.uniform(0.0,3.5,3)
#print "p2_x: %s"%p2_x
#p2_y = np.linspace(0.0,3.5,3)
p2_y = np.random.uniform(0.0,3.5,3)
#print "p2_y: %s"%p2_y
#p2_m = np.linspace(-1.0,3.5,20)
p2_m = np.random.uniform(-1.0,3.5,20)
#print "p2_m: %s"%p2_m
start = time.time()
kinGridRaw = BuildGrid(ssInit,p1_x,p1_y,p1_m,p2_x,p2_y,p2_m)
end = time.time() - start
times['mesh'] = end
for i,el in enumerate(kinGridRaw):
    print "coord %d: %s"%(i,str(el.shape))

def omegaFromSS(ss):
    #lab
    return (ss**2 - 1.0)/2.0

#initial particles

start = time.time()
omega = omegaFromSS(kinGridRaw[0])
end =  time.time() -start
times['om']=end
print "omega shape: %s"%(str(omega.shape))
#print "omega: %s"%omega

start =  time.time()
E = np.ones(omega.shape)
end =  time.time() - start
times['E'] = end
print "E shape: %s"%(str(E.shape))
#print "E: %s"%E

Et = omega + E
pt = omega
print "Et shape: %s"%(str(Et.shape))
#print "Et: %s"%Et
print "pt shape: %s"%(str(pt.shape))
#print "pt: %s"%pt
start =  time.time()
#P=qft.MinkowskiVector([E,np.zeros(E.shape),np.zeros(E.shape),np.zeros(E.shape)])
P=qft.MinkowskiVector([E,0.0,0.0,0.0])
end =  time.time() - start
times['Pfirst']=end

start =  time.time()
P3m = 0.5*(P._0() - P._3()) - kinGridRaw[3] - kinGridRaw[6]
P3x =  - kinGridRaw[1] - kinGridRaw[4]
P3y =  - kinGridRaw[2] - kinGridRaw[5]
end =  time.time() - start
times['p3coord'] = end

print "P3m shape: %s"%(str(P3m.shape))
print "P3x shape: %s"%(str(P3x.shape))
print "P3y shape: %s"%(str(P3y.shape))


def physArea(P1m,P2m,P3m):
    return (P1m>0) * (P2m>0) * (P3m>0) 


def BuildFinalMom(px,py,pm):
    #print pm
    pp = (px**2 + py**2 + 1)/(4.0*pm)
    return qft.MinkowskiVector(qft.parray([pp+pm,px,py,pp-pm]))

def buildAllMom(p1x,p1y,p1m,p2x,p2y,p2m,p3x,p3y,p3m):
    physAreaArr = physArea(p1m,p2m,p3m)
    print "physArea: %s"%(str(physAreaArr.shape))
    #print physAreaArr.all()==False
    p1xT = p1x[physAreaArr]
    p1yT = p1y[physAreaArr]
    p1mT = p1m[physAreaArr]
    #print "p1m: %s"%(str(p1m.shape))
    #print "p1mT: %s"%(str(p1mT.shape))
    p2xT = p2x[physAreaArr]
    p2yT = p2y[physAreaArr]
    p2mT = p2m[physAreaArr]
    #print "p2m: %s"%(str(p2m.shape))
    #print "p2mT: %s"%(str(p2mT.shape))
    p3xT = p3x[physAreaArr]
    p3yT = p3y[physAreaArr]
    p3mT = p3m[physAreaArr]
    print "p3m: %s"%(str(p3m.shape))
    print "p3mT: %s"%(str(p3mT.shape))
    P1 = BuildFinalMom(p1xT,p1yT,p1mT)
    P2 = BuildFinalMom(p2xT,p2yT,p2mT)
    P3 = BuildFinalMom(p3xT,p3yT,p3mT)
    return P1,P2,P3

start =  time.time()
Pa,Pb,Pc = buildAllMom(kinGridRaw[1],kinGridRaw[2],kinGridRaw[3],kinGridRaw[4],kinGridRaw[5],kinGridRaw[6],P3x,P3y,P3m)
end =  time.time() - start
times['finalMom'] = end

def buildInitMom(om,e,p1x,p1y,p1m,p2x,p2y,p2m,p3x,p3y,p3m):
    physAreaArr = physArea(p1m,p2m,p3m)
    omegaT = om[physAreaArr]
    ET = e[physAreaArr]
    #P=qft.MinkowskiVector([ET,np.zeros(ET.shape),np.zeros(ET.shape),np.zeros(ET.shape)])
    P=qft.MinkowskiVector([ET,0.0,0.0,0.0])
    K = qft.MinkowskiVector([omegaT,np.zeros(omegaT.shape),np.zeros(omegaT.shape),omegaT])
    return K,P

start =  time.time()
Ktest,Ptest = buildInitMom(omega,E,kinGridRaw[1],kinGridRaw[2],kinGridRaw[3],kinGridRaw[4],kinGridRaw[5],kinGridRaw[6],P3x,P3y,P3m)
end =  time.time() - start
times['initMom'] = end
print Ktest.shape
print Ptest.shape

coord 0: (1, 10, 10, 20, 3, 3, 20)
coord 1: (1, 10, 10, 20, 3, 3, 20)
coord 2: (1, 10, 10, 20, 3, 3, 20)
coord 3: (1, 10, 10, 20, 3, 3, 20)
coord 4: (1, 10, 10, 20, 3, 3, 20)
coord 5: (1, 10, 10, 20, 3, 3, 20)
coord 6: (1, 10, 10, 20, 3, 3, 20)
omega shape: (1, 10, 10, 20, 3, 3, 20)
E shape: (1, 10, 10, 20, 3, 3, 20)
Et shape: (1, 10, 10, 20, 3, 3, 20)
pt shape: (1, 10, 10, 20, 3, 3, 20)
P3m shape: (1, 10, 10, 20, 3, 3, 20)
P3x shape: (1, 10, 10, 20, 3, 3, 20)
P3y shape: (1, 10, 10, 20, 3, 3, 20)
physArea: (1, 10, 10, 20, 3, 3, 20)
p3m: (1, 10, 10, 20, 3, 3, 20)
p3mT: (3600,)
(3600,)
(3600,)


In [4]:

start = time.time()
J0obj = J0(Pa,Ptest,Ktest,mode='c')
times['initJ0'] = time.time() - start

start = time.time()
res1 = J0obj(2,1,1)
for s1 in (0,1):
    for s2 in (0,1):
        for mu in np.arange(4):
            J0obj(mu,s1,s2)

times['calcJ0'] = time.time() - start

calls = int(res1.shape[0])

print "no. calls: %d"%(calls)
print "time init: %1.2e (%1.2e  per call)"%(times['initJ0'],times['initJ0']/float(calls))
print "time calc: %1.2e (%1.2e  per call)"%(times['calcJ0'],times['calcJ0']/float(calls))

no. calls: 3600
time init: 2.40e-02 (6.67e-06  per call)
time calc: 1.21e-02 (3.37e-06  per call)


compare to serial
-------

In [5]:
import itertools
from sftrident import currentClass

SQkinPara=[t for t in itertools.product(ssInit,p1_x,p1_y,p1_m,p2_x,p2_y,p2_m)]
sqP = qft.MinkowskiVector([1.0,0.0,0.0,0.0])
ind = 0
err = 0

gammaMu = qft.GammaMatrix()


times['SQinitJ0'] = 0
times['SQcalcJ0'] = 0

currObj = currentClass({'a0':1e-4,'mass':1.0,'xi':0.0})

for i,el in enumerate(SQkinPara):
    sqOm = omegaFromSS(el[0])
    sqK = qft.MinkowskiVector([sqOm,0.0,0.0,sqOm])
    
    sqP3m = 0.5 - el[3] - el[6]
    sqP3x = - el[1] - el[4]
    sqP3y = - el[2] - el[5]
    if el[3]>0 and el[6] >0 and sqP3m>0:
        sqP1 = BuildFinalMom(el[1],el[2],el[3])
        sqP2 = BuildFinalMom(el[4],el[5],el[6])
        sqP3 = BuildFinalMom(sqP3x,sqP3y,sqP3m)
        
        start = time.time()
        sqU = np.array([qft.SpinorU((sqP,1.0),s) for s in (1,2)])
        sqU1b = np.array([qft.SpinorUBar((sqP1,1.0),2) for s in (1,2)])
        times['SQinitJ0'] += time.time() -start
        
        start = time.time()
        #sqJ0 = sqU1b*(gammaMu[2]*sqU)
        currObj.setKin(sqK,sqP1,sqP,sqU1b,sqU)
        sqJ0=currObj.evalJ0()[1]._2()
        times['SQcalcJ0'] += time.time() -start
        #print "-"*20
        #print "%s\n%s"%(res1[ind],sqJ0)
        if np.isclose(res1[ind],sqJ0).all():
            pass
        else:
            err+=1
        ind +=1

print "Done with %d errors."%err
for el in times.iterkeys():
    print "%s: %1.2e"%(el,times[el])
    print "-"*20

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [27.8720146   1.75547526  0.1579193  27.79824753]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorA[1]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [27.8720146   1.75547526  0.1579193  27.79824753]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorA[1]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]
-------
a0: 

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [7.58490671 1.75547526 0.1579193  7.30918449]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          2.93000115+0.j          0.59913808+0.05389735j
 -2.49460124+0.j        ]
spinorA[1]: [ 0.        +0.j          2.93000115+0.j          0.59913808+0.05389735j
 -2.49460124+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [7.58490671 1.75547526 0.1579193  7.30918449]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          2.93000115+0.j          0.59913808+0.05389735j
 -2.49460124+0.j        ]
spinorA[1]: [ 0.        +0.j          2.93000115+0.j          0.59913808+0.05389735j
 -2.49460124+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]
----

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [9.9629399  1.75547526 0.1579193  9.75466758]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.31103306+0.j          0.53018959+0.04769487j
 -2.94610999+0.j        ]
spinorA[1]: [ 0.        +0.j          3.31103306+0.j          0.53018959+0.04769487j
 -2.94610999+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [9.9629399  1.75547526 0.1579193  9.75466758]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.31103306+0.j          0.53018959+0.04769487j
 -2.94610999+0.j        ]
spinorA[1]: [ 0.        +0.j          3.31103306+0.j          0.53018959+0.04769487j
 -2.94610999+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
----

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [59.84239591  1.75547526  2.17753552 59.76862885]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          7.80015358+0.j          0.2250565 +0.27916572j
 -7.66249385+0.j        ]
spinorA[1]: [ 0.        +0.j          7.80015358+0.j          0.2250565 +0.27916572j
 -7.66249385+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [59.84239591  1.75547526  2.17753552 59.76862885]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          7.80015358+0.j          0.2250565 +0.27916572j
 -7.66249385+0.j        ]
spinorA[1]: [ 0.        +0.j          7.80015358+0.j          0.2250565 +0.27916572j
 -7.66249385+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [9.6132494  1.75547526 2.17753552 9.14282285]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.25779824+0.j          0.53885328+0.66840711j
 -2.80644232+0.j        ]
spinorA[1]: [ 0.        +0.j          3.25779824+0.j          0.53885328+0.66840711j
 -2.80644232+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [9.6132494  1.75547526 2.17753552 9.14282285]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.25779824+0.j          0.53885328+0.66840711j
 -2.80644232+0.j        ]
spinorA[1]: [ 0.        +0.j          3.25779824+0.j          0.53885328+0.66840711j
 -2.80644232+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]
----

...

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [22.82982216  2.77024397  1.95936318 22.55409994]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j         4.88157988+0.j         0.56748922+0.4013789j
 -4.620246  +0.j       ]
spinorA[1]: [ 0.        +0.j         4.88157988+0.j         0.56748922+0.4013789j
 -4.620246  +0.j       ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [22.82982216  2.77024397  1.95936318 22.55409994]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j         4.88157988+0.j         0.56748922+0.4013789j
 -4.620246  +0.j       ]
spinorA[1]: [ 0.        +0.j         4.88157988+0.j         0.56748922+0.4013789j
 -4.620246  +0.j       ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]
-------
a0: 

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [13.53522343  2.77024397  1.95936318 13.06479688]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.81250881+0.j          0.72661969+0.51393014j
 -3.42682405+0.j        ]
spinorA[1]: [ 0.        +0.j          3.81250881+0.j          0.72661969+0.51393014j
 -3.42682405+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [13.53522343  2.77024397  1.95936318 13.06479688]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.81250881+0.j          0.72661969+0.51393014j
 -3.42682405+0.j        ]
spinorA[1]: [ 0.        +0.j          3.81250881+0.j          0.72661969+0.51393014j
 -3.42682405+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [76.80039674  2.77024397  1.62818506 76.72662968]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          8.82045332+0.j          0.31407048+0.18459199j
 -8.69871728+0.j        ]
spinorA[1]: [ 0.        +0.j          8.82045332+0.j          0.31407048+0.18459199j
 -8.69871728+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [76.80039674  2.77024397  1.62818506 76.72662968]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          8.82045332+0.j          0.31407048+0.18459199j
 -8.69871728+0.j        ]
spinorA[1]: [ 0.        +0.j          8.82045332+0.j          0.31407048+0.18459199j
 -8.69871728+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [20.67526696  2.77024397  1.62818506 20.39954474]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          4.65567041+0.j          0.59502579+0.34972086j
 -4.38165569+0.j        ]
spinorA[1]: [ 0.        +0.j          4.65567041+0.j          0.59502579+0.34972086j
 -4.38165569+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [20.67526696  2.77024397  1.62818506 20.39954474]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          4.65567041+0.j          0.59502579+0.34972086j
 -4.38165569+0.j        ]
spinorA[1]: [ 0.        +0.j          4.65567041+0.j          0.59502579+0.34972086j
 -4.38165569+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [12.27241472  2.77024397  1.62818506 11.80198817]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.64313254+0.j          0.76040164+0.44691898j
 -3.23951655+0.j        ]
spinorA[1]: [ 0.        +0.j          3.64313254+0.j          0.76040164+0.44691898j
 -3.23951655+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [12.27241472  2.77024397  1.62818506 11.80198817]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j          3.64313254+0.j          0.76040164+0.44691898j
 -3.23951655+0.j        ]
spinorA[1]: [ 0.        +0.j          3.64313254+0.j          0.76040164+0.44691898j
 -3.23951655+0.j        ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 

Test $J_1$
======

In [6]:
def J12func(q1,q2,k,sp1,sp2,pol,a0,m,mu):
    term1 = sp1*((qft.feyndagg(pol)*qft.feyndagg(k))*gammaMu[mu])*sp2/(k*q1)
    term2 = sp1*((gammaMu[mu]*qft.feyndagg(k))*qft.feyndagg(pol))*sp2/(k*q2)
    return .5*a0*m*(term1 - term2)
    #return term2


start = time.time()
J1obj = J1(Pa,Ptest,Ktest,mode='c')
times['initJ1'] = time.time() - start

start = time.time()
res2 = J1obj(2,0,1)
for s1 in (0,1):
    for s2 in (0,1):
        for mu in np.arange(4):
            J1obj(mu,s1,s2)
times['calcJ1'] = time.time() - start

calls = int(res2.shape[0])

print "no. calls: %d"%(calls)
print "time init: %1.2e (%1.2e  per call)"%(times['initJ1'],times['initJ1']/float(calls))
print "time calc: %1.2e (%1.2e  per call)"%(times['calcJ1'],times['calcJ1']/float(calls))

no. calls: 3600
time init: 2.41e-02 (6.69e-06  per call)
time calc: 3.65e-01 (1.01e-04  per call)


compare with serial
-----

In [12]:
ind = 0
err = 0

gammaMu = qft.GammaMatrix()
pol1 = laserPolarisation(1)

currObj = currentClass({'a0':1e-4,'mass':1.0,'xi':0.0})

times['SQinitJ1'] = 0
times['SQcalcJ1'] = 0

errVal=0.0

for i,el in enumerate(SQkinPara):
    sqOm = omegaFromSS(el[0])
    sqK = qft.MinkowskiVector([sqOm,0.0,0.0,sqOm])
    sqP3m = 0.5 - el[3] - el[6]
    sqP3x = - el[1] - el[4]
    sqP3y = - el[2] - el[5]
    if el[3]>0 and el[6] >0 and sqP3m>0:
        sqP1 = BuildFinalMom(el[1],el[2],el[3])
        sqP2 = BuildFinalMom(el[4],el[5],el[6])
        sqP3 = BuildFinalMom(sqP3x,sqP3y,sqP3m)
        start = time.time()
        sqU = np.array([qft.SpinorU((sqP,1.0),s) for s in (1,2)])
        sqU1b = np.array([qft.SpinorUBar((sqP1,1.0),2) for s in (1,2)])
        times['SQinitJ1'] += time.time() -start
        
        start = time.time()
        #sqJ1 = J12func(sqP1,sqP,sqK,sqU1b,sqU,pol1,1e-4,1.0,2)
        currObj.setKin(sqK,sqP1,sqP,sqU1b,sqU)
        sqJ1=currObj.J1[1]._2()
        times['SQcalcJ1'] += time.time() -start
        #print "-"*20
        #print "%s\n%s"%(res2[ind],sqJ1)
        if np.isclose(res2[ind],sqJ1).all():
            pass
        else:
            err+=1
        #print "-"*20
        #print"%s\n%s"%(res2[:,ind],sqU1b[:])
        #if not(np.isclose(res2._0()[ind],sqP._0()).all()):
        #    err+=1
        #if not(np.isclose(res2._1()[ind],sqP._1()).all()):
        #    err+=1
        #if not(np.isclose(res2._2()[ind],sqP._2()).all()):
        #    err+=1
        #if not(np.isclose(res2._3()[ind],sqP._3()).all()):
        #    err+=1
        ind +=1

print "Done with %d errors."%err
for el in times.iterkeys():
    print "%s: %1.2e"%(el,times[el])
    print "-"*20

-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [27.8720146   1.75547526  0.1579193  27.79824753]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorA[1]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 1. 0. 0.]
-------
a0: 0.0001
mass: 1.0
xi: 0.0
momA: [27.8720146   1.75547526  0.1579193  27.79824753]
momB: [1. 0. 0. 0.]
spinorA[0]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorA[1]: [ 0.        +0.j         5.37326852+0.j         0.32670529+0.0293898j
 -5.17343353+0.j       ]
spinorB[0]: [1.41421356+0.j 0.        +0.j 0.        +0.j 0.        +0.j]
spinorB[1]: [0.        +0.j 1.41421356+0.j 0.        +0.j 0.        +0.j]
pol: [0. 0. 1. 0.]


TypeError: 'numpy.ndarray' object is not callable

Test $J_2$
=====

In [8]:
start = time.time()
J2obj = J2(Pa,Ptest,Ktest,mode='c')
times['initJ2'] = time.time() - start

start = time.time()
res3 = J2obj(2,1,1)
times['calcJ2'] = time.time() - start

calls = int(res3.shape[0])

print "no. calls: %d"%(calls)
print "time init: %1.2e (%1.2e  per call)"%(times['initJ2'],times['initJ2']/float(calls))
print "time calc: %1.2e (%1.2e  per call)"%(times['calcJ2'],times['calcJ2']/float(calls))

no. calls: 3600
time init: 2.50e-02 (6.94e-06  per call)
time calc: 2.10e-02 (5.84e-06  per call)


compare with serial
--------

In [9]:
ind = 0
err = 0

gammaMu = qft.GammaMatrix()
pol1 = laserPolarisation(2)


times['SQinitJ2'] = 0
times['SQcalcJ2'] = 0

errVal=0.0

for i,el in enumerate(SQkinPara):
    sqOm = omegaFromSS(el[0])
    sqK = qft.MinkowskiVector([sqOm,0.0,0.0,sqOm])
    sqP3m = 0.5 - el[3] - el[6]
    sqP3x = - el[1] - el[4]
    sqP3y = - el[2] - el[5]
    if el[3]>0 and el[6] >0 and sqP3m>0:
        sqP1 = BuildFinalMom(el[1],el[2],el[3])
        sqP2 = BuildFinalMom(el[4],el[5],el[6])
        sqP3 = BuildFinalMom(sqP3x,sqP3y,sqP3m)
        start = time.time()
        sqU = qft.SpinorU((sqP,1.0),2)
        sqU1b = qft.SpinorUBar((sqP1,1.0),2)
        times['SQinitJ2'] += time.time() -start
        
        start = time.time()
        sqJ2 = J12func(sqP1,sqP,sqK,sqU1b,sqU,pol1,1e-4,1.0,2)
        times['SQcalcJ2'] += time.time() -start
        print "-"*20
        print "%s\n%s"%(res3[ind],sqJ2)
        if np.isclose(res3[ind],sqJ2).all():
            pass
        else:
            err+=1
        #print "-"*20
        #print"%s\n%s"%(res2[:,ind],sqU1b[:])
        #if not(np.isclose(res2._0()[ind],sqP._0()).all()):
        #    err+=1
        #if not(np.isclose(res2._1()[ind],sqP._1()).all()):
        #    err+=1
        #if not(np.isclose(res2._2()[ind],sqP._2()).all()):
        #    err+=1
        #if not(np.isclose(res2._3()[ind],sqP._3()).all()):
        #    err+=1
        ind +=1

print "Done with %d errors."%err
for el in times.iterkeys():
    print "%s: %1.2e"%(el,times[el])
    print "-"*20

--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-0.00017742476888003153+0j)
(-0.00017742476888003188+0j)
--------------------
(-8.087359119873528e-05+0j)
(-8.08735911987353e-05+0j)
--------------------
(-8.087359119873528e-05+0j)
(-8.08735911987353e-05+0j)
--------------------
(-8.087359119873528e-05+0j)
(-8.08735911987353e-05+0j)
--------------------
(-8.087359119873528e-05+0j)
(-8.08735911

--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-0.0001147570100385257+0j)
(-0.00011475701003852515+0j)
--------------------
(-5.3903274740164344e-05+0j)
(-5.390327474016441e-05+0j)
--------------------
(-5.3903274740164344e-05+0j)
(-5.390327474016441e-05+0j)
--------------------
(-5.3903274740164344e-05+0j)
(-5.390327474016441e-05+0j)
--------------------
(-5.3903274740164344e-05+0j)
(-5.3903274740

--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-0.00017547100864518183+0j)
(-0.00017547100864518224+0j)
--------------------
(-8.007096548055322e-05+0j)
(-8.007096548055326e-05+0j)
--------------------
(-8.007096548055322e-05+0j)
(-8.007096548055326e-05+0j)
--------------------
(-8.007096548055322e-05+0j)
(-8.007096548055326e-05+0j)
--------------------
(-8.007096548055322e-05+0j)
(-8.00709

--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-0.00013954889215202706+0j)
(-0.000139548892152027+0j)
--------------------
(-6.486077746979808e-05+0j)
(-6.486077746979792e-05+0j)
--------------------
(-6.486077746979808e-05+0j)
(-6.486077746979792e-05+0j)
--------------------
(-6.486077746979808e-05+0j)
(-6.486077746979792e-05+0j)
--------------------
(-6.486077746979808e-05+0j)
(-6.486077746979792e-05+0j)

--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-9.02311071503262e-05+0j)
(-9.023110715032866e-05+0j)
--------------------
(-4.274792685704089e-05+0j)
(-4.274792685704082e-05+0j)
--------------------
(-4.274792685704089e-05+0j)
(-4.274792685704082e-05+0j)
--------------------
(-4.274792685704089e-05+0j)
(-4.274792685704082e-05+0j)
--------------------
(-4.274792685704089e-05+0j)
(-4.274792685704082e-05+0j)
--------

...

--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-8.69623590526673e-05+0j)
(-8.696235905266755e-05+0j)
--------------------
(-4.12404226470399e-05+0j)
(-4.12404226470401e-05+0j)
--------------------
(-4.12404226470399e-05+0j)
(-4.12404226470401e-05+0j)
--------------------
(-4.12404226470399e-05+0j)
(-4.12404226470401e-05+0j)
--------------------
(-4.12404226470399e-05+0j)
(-4.12404226470401e-05+0j)
----------------

--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-0.00012307625514631454+0j)
(-0.00012307625514631313+0j)
--------------------
(-5.7618558525404775e-05+0j)
(-5.7618558525404796e-05+0j)
--------------------
(-5.7618558525404775e-05+0j)
(-5.7618558525404796e-05+0j)
--------------------
(-5.7618558525404775e-05+0j)
(-5.7618558525404796e-05+0j)
--------------------
(-5.7618558525404775e-05+0j)
(-

--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-9.526635214137721e-05+0j)
(-9.526635214137596e-05+0j)
--------------------
(-4.5061103495615074e-05+0j)
(-4.506110349561511e-05+0j)
--------------------
(-4.5061103495615074e-05+0j)
(-4.506110349561511e-05+0j)
--------------------
(-4.5061103495615074e-05+0j)
(-4.506110349561511e-05+0j)
--------------------
(-4.5061103495615074e-05+0j)
(-4.506110349561511e-05

--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-0.00012241847796169882+0j)
(-0.0001224184779616988+0j)
--------------------
(-5.732616530563486e-05+0j)
(-5.732616530563488e-05+0j)
--------------------
(-5.732616530563486e-05+0j)
(-5.732616530563488e-05+0j)
--------------------
(-5.732616530563486e-05+0j)
(-5.732616530563488e-05+0j)
--------------------
(-5.732616530563486e-05+0j)
(-5.73261653056348

--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-0.00010808411892893006+0j)
(-0.00010808411892892951+0j)
--------------------
(-5.089701246855767e-05+0j)
(-5.089701246855768e-05+0j)
--------------------
(-5.089701246855767e-05+0j)
(-5.089701246855768e-05+0j)
--------------------
(-5.089701246855767e-05+0j)
(-5.089701246855768e-05+0j)
--------------------
(-5.089701246855767e-05+0j)
(-5.08970

In [10]:
print "%1.2e"%(1e-3*1e9/60/60/420*30)

1.98e+01


In [11]:
print"%1.2e"%(70**6)

1.18e+11
